# Example Visualizations of LILY Color Reflectance data.

The plots below are interactive. Hovering over datapoints will display additional information.

If they do not render on Github within the notebook they can also be found in the "plots" subfolder as html pages.

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import warnings

import scipy.stats

import hvplot
import hvplot.pandas
import datashader as ds
import panel as pn

# set maximum number of rows/columns to display in dataframes
pd.set_option("display.max_rows",200)
pd.set_option("display.max_columns",None)

warnings.filterwarnings('ignore')

In [2]:
# Note: the RSC file is ~1.2 GB in size and is not published here with this repo. Download the file from https://zenodo.org/record/8408297 once it is published.
df = pd.read_csv("./RSC_DataLITH.csv")
df.head()

Exp   Site Hole  Core Type Sect A/W  Offset (cm)  Depth CSF-A (m)  \
0  318  U1355    A     1    R    1   A         39.6            0.396   
1  318  U1355    A     1    R    1   A         29.5            0.295   
2  318  U1355    A     1    R    1   A         27.0            0.270   
3  318  U1355    A     1    R    1   A         24.5            0.245   
4  318  U1355    A     1    R    1   A         42.1            0.421   

   Depth CSF-B (m)  Reflectance L*  Reflectance a*  Reflectance b*  \
0            0.261            35.7             2.4             2.7   
1            0.195            38.6             2.0             2.3   
2            0.178            38.5             1.9             0.4   
3            0.162            37.2             1.8             2.9   
4            0.278            38.3             1.9             0.8   

   Tristimulus X  Tristimulus Y  Tristimulus Z  Normalized spectral data link  \
0            8.7            8.8            8.8                            NaN   
1           10.2           10.4           10.6                            NaN   
2           10.1           10.3           11.1                            NaN   
3            9.4            9.6            9.5                            NaN   
4           10.0           10.3           10.9                            NaN   

   Unnormalized spectral data link      Timestamp (UTC)  Instrument  \
0                              NaN  2010-01-21 15:08:47  OOUSB4000V   
1                              NaN  2010-01-21 15:08:47  OOUSB4000V   
2                              NaN  2010-01-21 15:08:47  OOUSB4000V   
3                              NaN  2010-01-21 15:08:47  OOUSB4000V   
4                              NaN  2010-01-21 15:08:47  OOUSB4000V   

  Instrument group      Text ID  Test No. Comments Sample comments  \
0            SHMSL  SHLF2067141  16376471      NaN             NaN   
1            SHMSL  SHLF2067141  16376471      NaN             NaN   
2            SHMSL  SHLF2067141  16376471      NaN             NaN   
3            SHMSL  SHLF2067141  16376471      NaN             NaN   
4            SHMSL  SHLF2067141  16376471      NaN             NaN   

   Test comments Result comments Prefix Principal Suffix Full Lithology  \
0            NaN             NaN    NaN      sand    NaN           sand   
1            NaN             NaN    NaN      sand    NaN           sand   
2            NaN             NaN    NaN      sand    NaN           sand   
3            NaN             NaN    NaN      sand    NaN           sand   
4            NaN             NaN    NaN      sand    NaN           sand   

  Simplified Lithology Lithology Type Degree of Consolidation  \
0                 sand    sedimentary          unconsolidated   
1                 sand    sedimentary          unconsolidated   
2                 sand    sedimentary          unconsolidated   
3                 sand    sedimentary          unconsolidated   
4                 sand    sedimentary          unconsolidated   

  Lithology Subtype Expanded Core Type  Latitude (DD)  Longitude (DD)  \
0           clastic                RCB     -63.841173      138.823783   
1           clastic                RCB     -63.841173      138.823783   
2           clastic                RCB     -63.841173      138.823783   
3           clastic                RCB     -63.841173      138.823783   
4           clastic                RCB     -63.841173      138.823783   

   Water Depth (mbsl)  
0             3729.04  
1             3729.04  
2             3729.04  
3             3729.04  
4             3729.04

In [3]:
df = df[['Reflectance L*',
       'Reflectance a*', 'Reflectance b*', 'Instrument',
       'Instrument group', 'Prefix',
       'Principal', 'Suffix','Simplified Lithology',
       'Lithology Type', 'Degree of Consolidation', 'Lithology Subtype',
       'Expanded Core Type']]

# Basic Statistics

In [4]:
# relative standard deviation
def rsd(x):
    return np.std(x) / np.mean(x)

# count of points outside 3 standard deviations of the mean
def outlier_count(x):
    return (np.abs(np.mean(x)-x) > 3*np.std(x)).sum()

# ratio of outliers to measurments
def outlier_count_ratio(x):
    return 100 * (np.abs(np.mean(x)-x) > 3*np.std(x)).sum() / len(x)
    

In [5]:
df_principal_stats = df[['Lithology Subtype','Principal', 'Reflectance L*']].groupby(['Lithology Subtype', 'Principal']).agg([
    'mean', 
    ('rsd', lambda x: rsd(x)), 
    'median', 'count',
    ('count_outliers',lambda x: outlier_count(x)),
    ('outlier_count_ratio %',lambda x: outlier_count_ratio(x)),
    ('kurtosis', lambda x: scipy.stats.kurtosis(x)),
    ('skew', lambda x: scipy.stats.skew(x))])

# retore single column index
df_principal_stats.columns = [x[1] for x in df_principal_stats.columns.to_flat_index()]
df_principal_stats = df_principal_stats.reset_index()

df_principal_stats.to_csv("./output/L_principal_stats.csv", index=False)

df_principal_stats 

Lithology Subtype          Principal       mean       rsd  median   count  \
0            biogenic  biosiliceous ooze  40.862425  0.170140  42.300    6689   
1            biogenic    calcareous ooze  58.261931  0.310768  61.345   20738   
2            biogenic     carbonate ooze  45.736840  0.208022  45.600   30546   
3            biogenic              chalk  61.149546  0.175014  61.210   28673   
4            biogenic              chert  32.829017  0.515541  30.400    1343   
..                ...                ...        ...       ...     ...     ...   
204             other           rudstone  50.089436  0.172725  50.600    2679   
205             other         wackestone  47.123497  0.152749  46.700  134142   
206         rodingite          rodingite  38.978000  0.084638  36.620       5   
207            schist             schist  45.448059  0.197155  47.170     953   
208      serpentinite       serpentinite  38.420392  0.359954  32.730      51   

     count_outliers  outlier_count_ratio %  kurtosis      skew  
0                40               0.597997  0.888202 -0.838642  
1                 0               0.000000 -1.632408 -0.063984  
2               542               1.774373  7.645544 -1.492684  
3               329               1.147421  0.405920 -0.629365  
4                 5               0.372301  0.225794  0.695743  
..              ...                    ...       ...       ...  
204               5               0.186637  0.035041 -0.194726  
205            1813               1.351553  2.275745  0.372845  
206               0               0.000000 -1.674443  0.472716  
207               5               0.524659  0.069834 -0.608132  
208               0               0.000000 -0.758424  0.601308  

[209 rows x 10 columns]

# Reflectance distributions by lithology

In [18]:
# distribution of reflectance values by principal lithology
hist = {'groupby': ['Principal'],
 'kind': 'hist',
 'y': ['Reflectance L*', 'Reflectance a*', 'Reflectance b*'],
 'xlim': (-20, 100),
 'height':500,
 'width':750,
 'bins':100,
 'title': 'Histogram by principal lithology'}

kde = {'groupby': ['Principal'],
 'kind': 'kde',
 'y': ['Reflectance L*', 'Reflectance a*', 'Reflectance b*'],
 'xlim': (-20, 100),
 'height':500,
 'width':500,
 'title': 'Kernel density by principal lithology'}

df = df.sort_values('Principal', ascending=True)
plot = df.hvplot(**hist) + df.hvplot(**kde)
#hvplot.save(plot, "./plots/reflectance_L_dist_by_principal.html")
plot

BokehModel(combine_events=True, render_bundle={'docs_json': {'34e473f2-9646-4861-8beb-e47d4469d0fe': {'version…

In [19]:
# distribution of reflectance values by prefix lithology
hist = {'groupby': ['Prefix'],
 'kind': 'hist',
 'y': ['Reflectance L*', 'Reflectance a*', 'Reflectance b*'],
 'xlim': (-20, 100),
 'height':500,
 'width':750,
 'bins':100,
 'ylabel':'reflectance',
 'title': 'Histogram by prefix lithology'}

kde = {'groupby': ['Prefix'],
 'kind': 'kde',
 'y': ['Reflectance L*', 'Reflectance a*', 'Reflectance b*'],
 'xlim': (-20, 100),
 'height':500,
 'width':500,
 'title': 'Kernel density by prefix lithology'}

df = df.sort_values('Principal', ascending=True)
df.hvplot(**hist) + df.hvplot(**kde)

BokehModel(combine_events=True, render_bundle={'docs_json': {'6b97f0b0-0040-49b7-9733-4ee9fa13f22b': {'version…

# Reflectance L* versus a* and b* for all nannofossil oozes.

In [9]:
# L* against b* values for all nannofossil oozes

plot = (df.query('Principal.str.lower().str.contains("nannofossil ooze")').hvplot.scatter(
    x='Reflectance b*', 
    y='Reflectance L*', 
    by='Principal', 
    alpha=0.2, 
    datashade=True, 
    height=500, 
    width=500, 
    subplots=True, 
    xlim=(-20,40),
    ylim=(0,100),
    aggregator='count'
    ) 
 
 + df.query('Principal.str.lower().str.contains("nannofossil ooze")').hvplot.scatter(
    x='Reflectance a*', 
    y='Reflectance L*', 
    by='Principal', 
    alpha=0.2, 
    datashade=True, 
    height=500, 
    width=500, 
    subplots=True, 
    xlim=(-20,40),
    ylim=(0,100),
    aggregator='count'
    )
)

plot

BokehModel(combine_events=True, render_bundle={'docs_json': {'e717b61d-d4eb-48ea-ac2e-63da7076c1f2': {'version…

# Reflectance L* boxplots of sedimentary lithologies by principal lithology and subtype.

Whiskers describe 95% confidence intervals.

In [12]:
# work just to be able to plot boxplots in order of mean L*
sorted_index = df[['Lithology Subtype','Principal','Reflectance L*']].groupby(['Lithology Subtype','Principal']).mean().sort_values('Reflectance L*', ascending=False).index
sorted_index_1 = [x[0] for x in sorted_index]
sorted_index_2 = [x[1] for x in sorted_index]

df['CustomOrder1'] = df['Lithology Subtype'].apply(lambda x: sorted_index_1.index(x))
df['CustomOrder2'] = df['Principal'].apply(lambda x: sorted_index_2.index(x))
df = df.sort_values('CustomOrder2', ascending=True).reset_index(drop=True)

In [13]:
boxplot = (df
            .query("`Lithology Type`.str.contains('sedimentary')")
           # .sort_values(['CustomOrder2','CustomOrder1'], ascending=[False, False])
            .hvplot.box(by=['Lithology Subtype', 'Principal'], y='Reflectance L*',width=2000, height=1000, ylim=(0,100), legend=False)
)

boxplot.opts(xrotation=45,
             box_color="Lithology Subtype",
             cmap='Category20',
             title='Reflectance L* boxplots by principal lithology for sedimentary type lithologies. Colored by lithological subtype.'
             )


#hvplot.save(boxplot, "./plots/reflectance_L_boxplot_by_principal_subtype.html")
boxplot

:BoxWhisker   [Lithology Subtype,Principal]   (Reflectance L*)

In [14]:
df_agg = df[['Principal','Prefix','Suffix','Reflectance L*']].groupby(['Principal','Prefix','Suffix']).mean('Reflectance L*').reset_index(drop=False)
df_agg

Principal                Prefix                   Suffix  Reflectance L*
0      andesite  amygdaloidal aphyric                    clast       29.800000
1      andesite               aphyric                    clast       46.687500
2      andesite                basalt                    clast       39.427778
3      andesite       feldspar phyric                    clast       43.180000
4      andesite        highly altered                    clast       40.200000
..          ...                   ...                      ...             ...
920  wackestone       glauconite-rich             with peloids       49.297778
921  wackestone           peloid-rich  with skeletal carbonate       47.000000
922  wackestone              skeletal        with foraminifera       44.804461
923  wackestone              skeletal          with glauconite       61.349206
924  wackestone              skeletal             with peloids       60.113143

[925 rows x 4 columns]

In [16]:
# hovering on a datapoint will display more information

boxplot = (df.sort_values('CustomOrder2')
           .hvplot.box(by='Principal', y='Reflectance L*',width=2000, height=1000, ylim=(0,100), legend=False) 
           * df_agg.hvplot.scatter(x='Principal', y='Reflectance L*', c='Prefix', legend=False, hover_cols=['Principal','Prefix','Suffix']))
boxplot.opts(xrotation=45,
             title='Reflectance L* boxplots by principal lithology, overlain with mean L* values of full Prefix-Principal-Suffix lithology'
             )

#hvplot.save(boxplot,"./plots/reflectance_L_boxplot_by_principal_overlain_with_full_lithology.html")

boxplot

:Overlay
   .BoxWhisker.I :BoxWhisker   [Principal]   (Reflectance L*)
   .Scatter.I    :Scatter   [Principal]   (Reflectance L*,Prefix,Suffix)